In [1]:
import pandas as pd
import numpy as np
import dask.dataframe as dd
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

from sklearn.model_selection import train_test_split, cross_val_score, cross_val_predict, GridSearchCV
from sklearn.preprocessing import StandardScaler, OneHotEncoder, LabelEncoder
from sklearn.metrics import classification_report, f1_score, precision_score, recall_score,\
precision_recall_curve, roc_auc_score, confusion_matrix, make_scorer, roc_curve, auc
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.feature_selection import SelectFromModel
import pickle
import gc
from datetime import datetime, date, time
from datetime import timedelta

pd.pandas.set_option('display.max_columns', None)
import warnings
warnings.simplefilter('ignore')

from sklearn.decomposition import PCA
import scipy.sparse
from sklearn.cluster import KMeans

In [2]:
TRAIN_DATASET_PATH = '/content/drive/MyDrive/Colab Notebooks/opportunities_train.xlsx'
train_df = pd.read_excel(TRAIN_DATASET_PATH)
train_df.tail()

id priority          lead_source  \
5820  6533cb93-3623-437a-b648-386961cbb47b    2 [2]      Сайт [web-site]   
5821  608bbe19-3eab-43aa-b94d-b5ad7a02b6a5    2 [2]        Почта [email]   
5822  a249c458-18fc-4ade-9b4c-a01140d4f9c8    2 [2]        Почта [email]   
5823  5342ac59-6506-46fa-a153-d3e3a2ab8d09    2 [2]        Почта [email]   
5824  a1df5704-f618-4d85-89c6-a6616385a647    3 [3]  Мероприятие [event]   

          reject_reason                                        description  \
5820  Не спам [no_spam]  Вопрос по работе с ПО Revit (интересуется как ...   
5821        Спам [spam]                                      нет описания    
5822  Не спам [no_spam]                                      нет описания    
5823  Не спам [no_spam]  Хранилище S3. Размещались на Амазоне ранее. Ск...   
5824  Не спам [no_spam]                                      нет описания    

                      product phone email industry web_form_of_consent  \
5820      Advanced [advanced]    да    да   Другое                  да   
5821                      нет    да    да   Другое                  да   
5822                      нет    да    да   Другое                  да   
5823  Enterprise [enterprise]    да    да   Другое                  да   
5824      Advanced [advanced]    да    да   Другое                  да   

     marketing_events                       status LeadMigration  \
5820              нет     Квалифицирован [success]   Нет [false]   
5821              нет  Неквалифицирован [rejected]   Нет [false]   
5822              нет  Неквалифицирован [rejected]   Нет [false]   
5823              нет     Квалифицирован [success]   Нет [false]   
5824              нет     Квалифицирован [success]   Нет [false]   

     converted_to_opportunity subsegment            createdAt  
5820                      NaN        NaN  28.06.2022 10:56:26  
5821                      нет        NaN  28.06.2022 10:00:28  
5822                      нет        NaN   28.06.2022 9:58:49  
5823                      NaN        NaN   28.06.2022 9:55:07  
5824                      NaN        NaN  16.06.2022 19:22:56

In [3]:
TEST_DATASET_PATH = '/content/drive/MyDrive/Colab Notebooks/opportunities_test.xlsx'
test_df = pd.read_excel(TEST_DATASET_PATH)
test_df.head(5)

id priority                  lead_source  \
0           44f2bcea-d770-45даd64a0611b    3 [3]              Сайт [web-site]   
1  28d3667f-8f6e-41a6-8f1f-53f18a304827    2 [2]              Сайт [web-site]   
2  eca86dc4-7d20-43f6-b851-e44f7d244420    2 [2]  Консультация [consultation]   
3  e85cb084-db84-451a-a409-abc6d367b261    2 [2]  Консультация [consultation]   
4  3be820bd-9ca4-4a8c-9164-e085743f51eb    2 [2]  Консультация [consultation]   

                                         description                  product  \
0                                      нет описания       Advanced [advanced]   
1  Здравствуйте. Нам требуются аналогичные ресурс...  Enterprise [enterprise]   
2                     Стоимость облачного хранилища.      Advanced [advanced]   
3  Занимаемся поиском поставщика облачного хранил...      Advanced [advanced]   
4                                      нет описания       Advanced [advanced]   

  phone email industry Согласие на рассылку [web_form_of_consent]  \
0    да    да   Другое                                         да   
1    да    да   Другое                                        нет   
2    да    да   Другое                                         да   
3    да    да   Другое                                         да   
4    да    да   Другое                                         да   

  Маркетинговые мероприятия [marketing_events]  \
0                                           да   
1                                          нет   
2                                          нет   
3                                          нет   
4                                          нет   

                         status [status] Миграционные лиды [LeadMigration]  \
0                            Новые [new]                       Нет [false]   
1  В работе у Сейлов [sales_in_progress]                       Нет [false]   
2  В работе у Сейлов [sales_in_progress]                       Нет [false]   
3               Квалифицирован [success]                       Нет [false]   
4               Квалифицирован [success]                       Нет [false]   

  Конвертирован в сделку [converted_to_opportunity]  \
0                                               нет   
1                                               нет   
2                                               нет   
3                                               нет   
4                                               нет   

             Подсегмент [subsegment]            createdAt  
0                                нет  21.02.2023 15:05:53  
1  Продуктовая заявка [product_form]  21.02.2023 12:12:23  
2                                нет  21.02.2023 12:06:32  
3                                нет  21.02.2023 10:58:54  
4                                нет  21.02.2023 10:05:42

In [4]:
train_df.dtypes #смотрим типы данных

id                          object
priority                    object
lead_source                 object
reject_reason               object
description                 object
product                     object
phone                       object
email                       object
industry                    object
web_form_of_consent         object
marketing_events            object
status                      object
LeadMigration               object
converted_to_opportunity    object
subsegment                  object
createdAt                   object
dtype: object

In [5]:
test_df=pd.read_excel(TEST_DATASET_PATH)
test_df.tail()

id priority      lead_source  \
13179  18128c1a-b4e1-407e-895a-f28250628e24    2 [2]    Почта [email]   
13180  f57f7342-813d-481c-88c0-145527b7f399    2 [2]    Почта [email]   
13181  c6e5162e-c49f-4098-8c98-3b370281ec66    2 [2]  Сайт [web-site]   
13182  6533cb93-3623-437a-b648-386961cbb47b    2 [2]  Сайт [web-site]   
13183  5342ac59-6506-46fa-a153-d3e3a2ab8d09    2 [2]    Почта [email]   

                                             description  \
13179  Интересны сервис рерайтер и суммаризатор для к...   
13180  Добрый день!\nСколько будет стоить аренда обла...   
13181  нужно разные услуги. Для начала из интересует ...   
13182  Вопрос по работе с ПО Revit (интересуется как ...   
13183  Хранилище S3. Размещались на Амазоне ранее. Ск...   

                       product phone email industry  \
13179       ML Space [mlspace]    да    да   Другое   
13180                      нет    да    да   Другое   
13181  Enterprise [enterprise]    да    да   Другое   
13182      Advanced [advanced]    да    да   Другое   
13183  Enterprise [enterprise]    да    да   Другое   

      Согласие на рассылку [web_form_of_consent]  \
13179                                         да   
13180                                         да   
13181                                         да   
13182                                         да   
13183                                         да   

      Маркетинговые мероприятия [marketing_events]           status [status]  \
13179                                           да  Квалифицирован [success]   
13180                                          нет  Квалифицирован [success]   
13181                                          нет  Квалифицирован [success]   
13182                                          нет  Квалифицирован [success]   
13183                                          нет  Квалифицирован [success]   

      Миграционные лиды [LeadMigration]  \
13179                       Нет [false]   
13180                       Нет [false]   
13181                       Нет [false]   
13182                       Нет [false]   
13183                       Нет [false]   

      Конвертирован в сделку [converted_to_opportunity]  \
13179                                               NaN   
13180                                               NaN   
13181                                               NaN   
13182                                               NaN   
13183                                               NaN   

      Подсегмент [subsegment]            createdAt  
13179                     NaN   29.06.2022 9:05:30  
13180                     NaN  28.06.2022 15:53:45  
13181                     NaN  28.06.2022 11:12:24  
13182                     NaN  28.06.2022 10:56:26  
13183                     NaN   28.06.2022 9:55:07

In [6]:
print('строк в трейне:', train_df.shape[0])
print('строк в тесте:', test_df.shape[0])

строк в трейне: 5825
строк в тесте: 13184


In [7]:
test_df.shape[1] - 1 == train_df.shape[1]

False

Целевым значением для нас будет значение "reject_reason" - то, является ли заявка спамом или нет. Вынесем этот столбец в отдельную переменную y, а в переменную X запишем все столбцы из таблицы кроме столбца target (reject_reason):

In [8]:
target = "reject_reason"

y = train_df[target]
X = train_df.drop(target, axis=1)

In [9]:
X.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5825 entries, 0 to 5824
Data columns (total 15 columns):
 #   Column                    Non-Null Count  Dtype 
---  ------                    --------------  ----- 
 0   id                        5825 non-null   object
 1   priority                  5825 non-null   object
 2   lead_source               5825 non-null   object
 3   description               5825 non-null   object
 4   product                   5825 non-null   object
 5   phone                     5825 non-null   object
 6   email                     5825 non-null   object
 7   industry                  5825 non-null   object
 8   web_form_of_consent       5825 non-null   object
 9   marketing_events          5825 non-null   object
 10  status                    5825 non-null   object
 11  LeadMigration             5825 non-null   object
 12  converted_to_opportunity  4307 non-null   object
 13  subsegment                1581 non-null   object
 14  createdAt               

Почистим данные. Колнку subsegment удалим, т.к. в ней отсутствует много значений

In [10]:
X.drop(['subsegment', 'id'], axis=1, inplace=True)

В столбце 'converted_to_opportunity' тоже есть пропущенные значения. Посмотрим, как часто встречаются возможные значения этого поля в датасете:

In [11]:
X['converted_to_opportunity'].value_counts()

нет    3979
да      328
Name: converted_to_opportunity, dtype: int64

Заполним пропуски значением "нет", т.к. его большинство


In [12]:
X['converted_to_opportunity'].fillna('нет', inplace=True)

In [13]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5825 entries, 0 to 5824
Data columns (total 13 columns):
 #   Column                    Non-Null Count  Dtype 
---  ------                    --------------  ----- 
 0   priority                  5825 non-null   object
 1   lead_source               5825 non-null   object
 2   description               5825 non-null   object
 3   product                   5825 non-null   object
 4   phone                     5825 non-null   object
 5   email                     5825 non-null   object
 6   industry                  5825 non-null   object
 7   web_form_of_consent       5825 non-null   object
 8   marketing_events          5825 non-null   object
 9   status                    5825 non-null   object
 10  LeadMigration             5825 non-null   object
 11  converted_to_opportunity  5825 non-null   object
 12  createdAt                 5825 non-null   object
dtypes: object(13)
memory usage: 591.7+ KB


Чтобы использовать категориальные признаки в нашей модели, нужно перевести их в числовые. С колонками, в которых всего два варианта проще. У нас это 'phone', email, marketing_events, web_form_of_consent, LeadMigration, converted_to_opportunity

In [14]:
X['converted_to_opportunity'].unique()

array(['нет', 'да'], dtype=object)

Заменим их на числовые значения 0 и 1

In [15]:
phone_map = {
    'да': 1,
    'нет': 0,
}

X['phone'] = X['phone'].map(phone_map)

In [16]:
email_map = {
    'да': 1,
    'нет': 0,
}

X['email'] = X['email'].map(email_map)

In [17]:
marketing_events_map = {
    'да': 1,
    'нет': 0,
}

X['marketing_events'] = X['marketing_events'].map(marketing_events_map)

In [18]:
web_form_of_consent_map = {
    'да': 1,
    'нет': 0,
}

X['web_form_of_consent'] = X['web_form_of_consent'].map(web_form_of_consent_map)

In [19]:
LeadMigration_map = {
    'Да [true]': 1,
    'Нет [false]': 0,
}

X['LeadMigration'] = X['LeadMigration'].map(LeadMigration_map)

In [20]:
converted_to_opportunity_map = {
    'да': 1,
    'нет': 0,
}

X['converted_to_opportunity'] = X['converted_to_opportunity'].map(converted_to_opportunity_map)

In [21]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5825 entries, 0 to 5824
Data columns (total 13 columns):
 #   Column                    Non-Null Count  Dtype 
---  ------                    --------------  ----- 
 0   priority                  5825 non-null   object
 1   lead_source               5825 non-null   object
 2   description               5825 non-null   object
 3   product                   5825 non-null   object
 4   phone                     5825 non-null   int64 
 5   email                     5825 non-null   int64 
 6   industry                  5825 non-null   object
 7   web_form_of_consent       5825 non-null   int64 
 8   marketing_events          5825 non-null   int64 
 9   status                    5825 non-null   object
 10  LeadMigration             5825 non-null   int64 
 11  converted_to_opportunity  5825 non-null   int64 
 12  createdAt                 5825 non-null   object
dtypes: int64(6), object(7)
memory usage: 591.7+ KB


In [22]:
X['product'].unique()

array(['ML Space [mlspace]', 'Advanced [advanced]',
       'Enterprise [enterprise]', 'нет', 'нет '], dtype=object)

Есть столбцы, которые содержат более двух категорий, поэтому переводить их в числовые значения нельзя. Для них используем dummy-переменные. Вместо одной переменной 'product' заведём четыре переменных. В каждом из этих столбцов теперь будет стоять 1, если у соответствующего объекта переменная 'product' равна этому значению, и 0, если нет

In [24]:
X = pd.get_dummies(X)

X.head(5)

phone  email  web_form_of_consent  marketing_events  LeadMigration  \
0      1      1                    1                 0              0   
1      1      0                    1                 0              0   
2      1      1                    1                 0              0   
3      1      1                    0                 0              0   
4      1      1                    1                 0              0   

   converted_to_opportunity  priority_1 [1]  priority_2 [2]  priority_3 [3]  \
0                         0               0               1               0   
1                         0               0               1               0   
2                         1               0               1               0   
3                         0               0               1               0   
4                         0               0               1               0   

   priority_4 [4]  lead_source_Naumen [nsd]  lead_source_SBBOL [sbbol]  \
0               0                         0                          0   
1               0                         1                          0   
2               0                         0                          0   
3               0                         0                          0   
4               0                         0                          0   

   lead_source_Вебинар [webinar]  lead_source_Звонок [call]  \
0                              0                          1   
1                              0                          0   
2                              0                          0   
3                              0                          0   
4                              0                          0   

   lead_source_Исследование [research]  \
0                                    0   
1                                    0   
2                                    0   
3                                    0   
4                                    0   

   lead_source_Клиент партнера [partner_client]  \
0                                             0   
1                                             0   
2                                             0   
3                                             0   
4                                             0   

   lead_source_Консультация [consultation]  \
0                                        0   
1                                        0   
2                                        1   
3                                        0   
4                                        1   

   lead_source_Личный контакт [networking]  lead_source_Мероприятие [event]  \
0                                        0                                0   
1                                        0                                0   
2                                        0                                0   
3                                        0                                0   
4                                        0                                0   

   lead_source_Миграция данных [migration]  lead_source_Партнер [partner]  \
0                                        0                              0   
1                                        0                              0   
2                                        0                              0   
3                                        0                              0   
4                                        0                              0   

   lead_source_Полка банка [bank]  lead_source_Почта [email]  \
0                               0                          0   
1                               0                          0   
2                               0                          0   
3                               0                          0   
4                               0                          0   

   lead_source_Сайт [web-site]  lead_source_Чат-бот [chatbot]  \
0                            0          

In [25]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5825 entries, 0 to 5824
Columns: 6438 entries, phone to createdAt_31.12.2022 1:03:40
dtypes: int64(6), uint8(6432)
memory usage: 36.0 MB
